In [1]:
import numpy as np
import menpo.io as mio
#import scipy.io as sio
from pathlib import Path
import os.path
import errno
#import menpo.shape
#%matplotlib inline
import re
from shutil import copyfile
import fnmatch
from PIL import Image
import json
from pprint import pprint
from datetime import datetime

In [2]:
import gspread
from oauth2client.service_account import ServiceAccountCredentials

<b> Export thumbnails for annotation </b>

In [ ]:
root = '/vol/phoebe/3DMD_SCIENSE_MUSEUM/15_06_2017/'
# root = '/media/ap112/My Passport/22_06_2017/'
dest='/media/ap112/C4184698184688FE/Dropbox/PostDoc/'

num_images=0
num_imgs=[]
size= 640, 480
ilevel=1
num_bmp=0
num_obj=0

# if os.direxists(os.path.join(os.getcwd()), 'new_folder'))
for path, dirs, files in os.walk(root):
    if ilevel==1:
        subjects=dirs
        folder_name=path.split('/')[-2]
        print(path,dirs,files,'folder name is',folder_name)        
    ilevel=ilevel+1
    for name in files:
        if fnmatch.fnmatch(name, '*.bmp'):
            num_images=num_images+1
    if 'meshes' in path.split('/')[-1]:
        for name in files:
#             e = time()
            if fnmatch.fnmatch(name, '*.bmp'):
                
                tmp_name=name.split('/')
#                 old_name=new_name[0]
                new_name=tmp_name[-1].split('.')
                new_path=dest+folder_name+'/'+new_name[0]
#                 print(new_path,'Old name is' ,old_name,new_name)
                if not os.path.exists(new_path):
                    os.makedirs(new_path)
                im = Image.open(path+'/'+name)
                im.thumbnail(size, Image.ANTIALIAS)
                
                im.save(new_path+'/'+new_name[0]+'.'+new_name[1]+'.jpg',quality=90)
                num_bmp=num_bmp+1
#                 print(time() - e)
            if fnmatch.fnmatch(name, '*.obj'):
                num_obj=num_obj+1
#             if old_name != new_name[0]:
#                 print(old_name+' has just finished')


<b> Change json files of a session</b>

In [ ]:
source_path='/vol/atlas/databases/3DMD_SCIENSE_MUSEUM/'
session_name = '04_05_2017'
dest_path_jsons='/vol/phoebe/NEW_3DMD/'
# /vol/atlas has been mapped to Z:
# /vol/phoebe has been mapped to P:
# Relative path for the exporting directory, the path that bmps has been exported
# as it should be written to json file
exportdirectory_path='Z:/databases/3DMD_SCIENSE_MUSEUM'

# Absolute paths for calibrations and mstereo.ini
# destination root path
dest_root_path='P:/NEW_3DMD'
calibations_path=''.join([dest_root_path,'/calibrations'])
mstereo_path=''.join([dest_root_path,'/Mstereo/mstereo_default.ini']) 
#  Absolyte path to back up all the old json files,
#  old json files are also backed up in the same folder changing just the extension
backupjson_path=''.join([dest_path_jsons,session_name,'/backupjson'])


num_images=0
num_imgs=[]
ilevel=1
num_copied=0 

for path, dirs, files in os.walk(''.join([source_path,session_name])):
    if ilevel==1:
        subjects=dirs
#         folder_name=path.split('/')[-1]
        print(path,dirs,files)    
    ilevel+=1
    for name in files:
        if fnmatch.fnmatch(name, '*.json') and len(name.split('.'))==2:
            
            num_images+=1
            source_filename=''.join([path,'/',name])
#             dest_filename=''.join([path,'/',name.split('.')[0],'.bak'])
            dest_filename=''.join([backupjson_path,'/',name])
            if not os.path.exists(os.path.dirname(dest_filename)):
                try:
                    os.makedirs(os.path.dirname(dest_filename))
                except OSError as exc: # Guard against race condition
                    if exc.errno != errno.EEXIST:
                        raise
            print(dest_filename)
#             if os.path.isfile(source_filename):
#                 copyfile(source_filename, dest_filename)
#                 copyfile(source_filename, dest_filename2)
#                 print(source_filename,' copied to ',dest_filename)
#                 print(dest_filename2)
#                 num_copied=num_copied+1
            with open(path+'/'+name) as data_file:    
                data = json.load(data_file)
                data_file.close() # Close the JSON file

#              old format
            exportdirectory=''.join([exportdirectory_path,'/',session_name,'/',name.split('.')[0]]) 
            if os.path.exists(exportdirectory+'/images'):
#             data["exportdirectory"] = ''.join([exportdirectory_path,'/',session_name,'/',name.split('.')[0]]) 
                data["exportdirectory"] = ''.join([exportdirectory,'/images']) 
            else:
                data["exportdirectory"] = exportdirectory 


#             print('exportdirectory: ',data["exportdirectory"])
            data["exportmstereoini"]=mstereo_path
#             print('exportmstereoini: ',data["exportmstereoini"])
            data["exporttkadir"]=''.join([calibations_path,'/', data["exporttkadir"].split('/')[-1]])
#             print('exporttkadir: ',data["exporttkadir"])
            data["exportmeshdir"]=''.join([dest_root_path,'/',session_name,'/',name.split('.')[0],'/meshes'])  #'P:/NEW_3DMD/10_04_2017/00002/"
            data.pop('exportimagedir', None)
#             print('exportmeshdir: ',data["exportmeshdir"])
#             print(data)
## Save our changes to JSON file
#             if name=='00001.json':
#                   print('00001.json')
            with open(dest_filename, 'w') as outfile:  
                json.dump(data, outfile)
                outfile.close()

In [ ]:
with open('/vol/atlas/databases/3DMD_SCIENSE_MUSEUM/11_05_2017/02075/02075.json') as data_file:
     data = json.load(data_file)
     data_file.close()

<b>Functions used to handle Google Spreadsheet</b>

In [3]:
# use creds to create a client to interact with the Google Drive API
def read_google_sheets(spreadsheet_name):
    scope = ['https://spreadsheets.google.com/feeds']
    creds = ServiceAccountCredentials.from_json_keyfile_name('client_secret.json', scope)
    client = gspread.authorize(creds)
 
    # Find a workbook by name and open the first sheet
    # Make sure you use the right name here.
    sheet = client.open(spreadsheet_name).sheet1
 
    # Extract and print all of the values
    list_of_hashes = sheet.get_all_records()
    list_of_hashes=list(filter(lambda x: x['Id']!='', list_of_hashes))
    # a = [x for x in new_list if x['Id'] != 250]
    return list_of_hashes

def searchdate(search_year, people):
        return [element for element in people if datetime.strptime(element['DateBirth'],'%d/%m/%Y').year<search_year]

def searchbetweenages(lower_limit,upper_limit ,people):
        return [element for element in people if datetime.strptime(element['DateBirth'],'%d/%m/%Y').year>lower_limit and datetime.strptime(element['DateBirth'],'%d/%m/%Y').year<upper_limit ]


def searchidn(idn, people):
    return [element for element in people if element['Gender'] == idn]

def searchnogender(people):
    return [element for element in people if element['Gender'] != 'Male' and element['Gender'] != 'Female']


def copy_obj_bmp2jpg_files(root_path,dest_path,list_of_people,type_image_file='jpg'):
    exist_lists=[]
    num_copied_subj=0
    num_not_found_subj=0
    not_found_list=[]
    if not os.path.exists(os.path.dirname(dest_path)):
        try:
            os.makedirs(os.path.dirname(dest_path))
        except OSError as exc: # Guard against race condition
            if exc.errno != errno.EEXIST:
                raise
    for person in list_of_people:
    #Transform the date to the one that is used for folders, namely dd_mm_yyyy
        if person['Id']<250:
            dt=datetime.strptime(person['Timestamp'],'%d/%m/%Y')
        else:
            dt=datetime.strptime(person['Timestamp'],'%d/%m/%Y %X')
        if dt.day<10:
            tmpday=''.join(['0',str(dt.day)])
        else:
            tmpday=str(dt.day)
        date_session=''.join([tmpday,'_0',str(dt.month),'_',str(dt.year)])
        #Check if  there is zero padding
        zeroes_padding=num_zeroes_in_filename(''.join([root_path,date_session]),str(person['Id']))
        if zeroes_padding==-1: 
            print(''.join([date_session,'/',str(person['Id'])]),'cannot be found')
            num_not_found_subj+=1
            not_found_list.append(person['Id'])
            continue
        
        fileid=str(person['Id']).rjust(zeroes_padding,'0')
        source_path=''.join([root_path,date_session,'/',fileid,'/meshes/'])
        if os.path.exists(os.path.dirname(source_path)):
#           find the first bmp  
            list_of_bmps=[]
            list_of_bmps=[x for x in os.listdir(source_path) if x.split('.')[-1]=='bmp']
            if len(t)!=0:
                sorted_list_of_bmps=sorted(list_of_bmps)
                if not os.path.exists(os.path.dirname(dest_path+'/'+fileid+'/')):
                                      try:
                                          os.makedirs(os.path.dirname(dest_path+'/'+fileid+'/'))
                                      except OSError as exc: # Guard against race condition
                                          if exc.errno != errno.EEXIST:
                                              raise
                for bmp_file in sorted_list_of_bmps:
#                     filename=''.join([fileid,'.',sorted(t)[0].split('.')[1]])
                    filename=''.join([fileid,'.',bmp_file.split('.')[1]])
        #             filename=''.join([fileid,'.000001'])   
                    bmpfilename=''.join([filename,'.bmp'])
#                     objfile=''.join([filename,'.obj'])
                    if os.path.isfile(source_path+bmpfilename):
#                                   print(source_path+bmpfile,source_path+objfile,' are copying')
                                  num_copied_subj+=1
#                                   copyfile(source_path+objfile, dest_path+objfile)
                                  
#                                   copyfile(source_path+objfile, dest_path+'/'+fileid+'/'+objfile)
                                  im = Image.open(source_path+bmpfilename)
                                  if (type_image_file=='jpg'):
                                        im.save(dest_path+filename+'.jpg',quality=90)
                                  elif  (type_image_file=='png'):
#                                         im.save(dest_path+filename+'.png','PNG')
                                          im.save(dest_path+'/'+fileid+'/'+filename+'.png','PNG')
                    print(source_path+bmpfilename,' is copying')
            list_of_objs=[]
            list_of_objs=[x for x in os.listdir(source_path) if x.split('.')[-1]=='obj']
            if len(list_of_objs)!=0:
                sorted_list_of_objs=sorted(list_of_objs)
                if not os.path.exists(os.path.dirname(dest_path+'/'+fileid+'/')):
                                      try:
                                          os.makedirs(os.path.dirname(dest_path+'/'+fileid+'/'))
                                      except OSError as exc: # Guard against race condition
                                          if exc.errno != errno.EEXIST:
                                              raise
                for obj_file in t:
                    filename=''.join([fileid,'.',obj_file.split('.')[1]])
                    objfilename=''.join([filename,'.obj'])
                    if os.path.isfile(source_path+objfilename):
                                  copyfile(source_path+objfilename, dest_path+'/'+fileid+'/'+objfilename)
                    print(source_path+objfilename,' are copying')
#                 print(source_path+bmpfile,source_path+objfile,' are copying')

                exist_lists.append(source_path)
    return num_not_found_subj,num_copied_subj,not_found_list

def batch_copy_transform(root_path,dest_path,list_folders,type_image_file='jpg'):
    exist_lists=[]
    num_copied_subj=0
    num_not_found_subj=0
    not_found_list=[]
    if not os.path.exists(os.path.dirname(dest_path)):
        try:
            os.makedirs(os.path.dirname(dest_path))
        except OSError as exc: # Guard against race condition
            if exc.errno != errno.EEXIST:
                raise
    for date_session in list_folders:
        list_subjects=sorted(os.listdir(root_path+date_session))
        for fileid in list_subjects:
            source_path=''.join([root_path,date_session,'/',fileid,'/meshes/'])
            if os.path.exists(os.path.dirname(source_path)):
                list_of_bmps=[]
                list_of_bmps=[x for x in os.listdir(source_path) if x.split('.')[-1]=='bmp']
                if len(list_of_bmps)!=0:
                    sorted_list_of_bmps=sorted(list_of_bmps)
                    if not os.path.exists(os.path.dirname(dest_path+'/'+fileid+'/')):
                                      try:
                                          os.makedirs(os.path.dirname(dest_path+'/'+fileid+'/'))
                                      except OSError as exc: # Guard against race condition
                                          if exc.errno != errno.EEXIST:
                                              raise
                    for bmp_file in sorted_list_of_bmps:
                        filename=''.join([fileid,'.',bmp_file.split('.')[1]])
                        bmpfilename=''.join([filename,'.bmp'])
                        if os.path.isfile(source_path+bmpfilename):
                                  im = Image.open(source_path+bmpfilename)
                                  if (type_image_file=='jpg'):
                                        im.save(dest_path+filename+'.jpg',quality=90)
                                  elif  (type_image_file=='png'):
                                          im.save(dest_path+'/'+fileid+'/'+filename+'.png','PNG')
                        print(source_path+bmpfilename,' is copying')
                list_of_objs=[]
                list_of_objs=[x for x in os.listdir(source_path) if x.split('.')[-1]=='obj']
                if len(list_of_objs)!=0:
                    sorted_list_of_objs=sorted(list_of_objs)
                    if not os.path.exists(os.path.dirname(dest_path+'/'+fileid+'/')):
                                      try:
                                          os.makedirs(os.path.dirname(dest_path+'/'+fileid+'/'))
                                      except OSError as exc: # Guard against race condition
                                          if exc.errno != errno.EEXIST:
                                              raise
                    for obj_file in sorted_list_of_objs:
                        filename=''.join([fileid,'.',obj_file.split('.')[1]])
                        objfilename=''.join([filename,'.obj'])
                        if os.path.isfile(source_path+objfilename):
                                  copyfile(source_path+objfilename, dest_path+'/'+fileid+'/'+objfilename)
                        print(source_path+objfilename,' are copying')
            
def num_zeroes_in_filename(file_path,person_id):
    len_id=len(person_id)
    if  os.path.exists(''.join([file_path,'/',person_id])):
            return len_id
    elif  os.path.exists(''.join([file_path,'/0',person_id])):
            return len_id+1
    elif  os.path.exists(''.join([file_path,'/00',person_id])):
            return len_id+2
    elif  os.path.exists(''.join([file_path,'/000',person_id])):
            return len_id+3
    elif  os.path.exists(''.join([file_path,'/0000',person_id])):
            return len_id+4
    else: 
            return -1
def printonekey(printedkeys,people):
    for person in people:
        for prkey in printedkeys:
            print(person[prkey])

In [4]:
spreadsheet_name= "Copy Museum data"

list_of_hashes=read_google_sheets(spreadsheet_name)

In [ ]:
copy_obj_bmp2jpg_files('/vol/phoebe/NEW_3DMD/','/media/ap112/Seagate Backup Plus Drive1/Seagate/3DMD/',list_of_hashes,'png')

In [6]:
batch_copy_transform('/vol/phoebe/3DMD_SCIENCE_MUSEUM/','/media/ap112/Seagate Backup Plus Drive/3DMD',list_sessions[40:-2],'png')

/vol/phoebe/3DMD_SCIENCE_MUSEUM/21_04_2017/00739/meshes/00739.000001.bmp  is copying
/vol/phoebe/3DMD_SCIENCE_MUSEUM/21_04_2017/00739/meshes/00739.000002.bmp  is copying
/vol/phoebe/3DMD_SCIENCE_MUSEUM/21_04_2017/00739/meshes/00739.000003.bmp  is copying
/vol/phoebe/3DMD_SCIENCE_MUSEUM/21_04_2017/00739/meshes/00739.000004.bmp  is copying
/vol/phoebe/3DMD_SCIENCE_MUSEUM/21_04_2017/00739/meshes/00739.000005.bmp  is copying
/vol/phoebe/3DMD_SCIENCE_MUSEUM/21_04_2017/00739/meshes/00739.000006.bmp  is copying
/vol/phoebe/3DMD_SCIENCE_MUSEUM/21_04_2017/00739/meshes/00739.000007.bmp  is copying
/vol/phoebe/3DMD_SCIENCE_MUSEUM/21_04_2017/00739/meshes/00739.000008.bmp  is copying
/vol/phoebe/3DMD_SCIENCE_MUSEUM/21_04_2017/00739/meshes/00739.000009.bmp  is copying
/vol/phoebe/3DMD_SCIENCE_MUSEUM/21_04_2017/00739/meshes/00739.000010.bmp  is copying
/vol/phoebe/3DMD_SCIENCE_MUSEUM/21_04_2017/00739/meshes/00739.000011.bmp  is copying
/vol/phoebe/3DMD_SCIENCE_MUSEUM/21_04_2017/00739/meshes/00739.000

FileNotFoundError: [Errno 2] No such file or directory: '/vol/phoebe/3DMD_SCIENCE_MUSEUM/26_05_2017/02824/meshes/'

In [11]:
list_sessions=sorted(os.listdir('/vol/phoebe/3DMD_SCIENCE_MUSEUM/'))
print(len(list_sessions))
print(list_sessions)

68
['01_05_2017', '01_06_2017', '01_07_2017', '02_06_2017', '02_07_2017', '03_06_2017', '04_05_2017', '04_06_2017', '05_05_2017', '05_06_2017', '06_05_2017', '07_05_2017', '08_05_2017', '08_06_2017', '09_06_2017', '10_04_2017', '10_06_2017', '11_04_2017', '11_05_2017', '11_06_2017', '12_04_2017', '12_05_2017', '12_06_2017', '13_04_2017', '13_05_2017', '14_04_2017', '14_05_2017', '15_04_2017', '15_05_2017', '15_06_2017', '16_04_2017', '16_06_2017', '17_04_2017', '17_06_2017', '18_05_2017', '18_06_2017', '19_05_2017', '19_06_2017', '20_04_2017', '20_05_2017', '21_04_2017', '21_05_2017', '22_04_2017', '22_05_2017', '22_06_2017', '23_04_2017', '23_06_2017', '24_04_2017', '24_06_2017', '25_05_2017', '25_06_2017', '26_05_2017', '26_06_2017', '27_04_2017', '27_05_2017', '27_06_2017', '28_04_2017', '28_05_2017', '28_06_2017', '29_04_2017', '29_05_2017', '29_06_2017', '30_04_2017', '30_06_2017', '31_05_2017', 'GenderBased', 'Mstereo', 'calibrations']


In [ ]:
below_18=searchbetweenages(1998,2017,list_of_hashes)

In [13]:
print(list_sessions[50:-2])

['26_05_2017', '26_06_2017', '27_05_2017', '27_06_2017', '28_05_2017', '28_06_2017', '29_05_2017', '29_06_2017', '30_06_2017', '31_05_2017']


In [12]:
batch_copy_transform('/vol/phoebe/3DMD_SCIENCE_MUSEUM/','/media/ap112/Seagate Backup Plus Drive/3DMD',list_sessions[50:-2],'png')

/vol/phoebe/3DMD_SCIENCE_MUSEUM/26_05_2017/02802/meshes/02802.000001.bmp  is copying
/vol/phoebe/3DMD_SCIENCE_MUSEUM/26_05_2017/02802/meshes/02802.000002.bmp  is copying
/vol/phoebe/3DMD_SCIENCE_MUSEUM/26_05_2017/02802/meshes/02802.000003.bmp  is copying
/vol/phoebe/3DMD_SCIENCE_MUSEUM/26_05_2017/02802/meshes/02802.000004.bmp  is copying
/vol/phoebe/3DMD_SCIENCE_MUSEUM/26_05_2017/02802/meshes/02802.000005.bmp  is copying
/vol/phoebe/3DMD_SCIENCE_MUSEUM/26_05_2017/02802/meshes/02802.000006.bmp  is copying
/vol/phoebe/3DMD_SCIENCE_MUSEUM/26_05_2017/02802/meshes/02802.000007.bmp  is copying
/vol/phoebe/3DMD_SCIENCE_MUSEUM/26_05_2017/02802/meshes/02802.000008.bmp  is copying
/vol/phoebe/3DMD_SCIENCE_MUSEUM/26_05_2017/02802/meshes/02802.000009.bmp  is copying
/vol/phoebe/3DMD_SCIENCE_MUSEUM/26_05_2017/02802/meshes/02802.000010.bmp  is copying
/vol/phoebe/3DMD_SCIENCE_MUSEUM/26_05_2017/02802/meshes/02802.000011.bmp  is copying


KeyboardInterrupt: 

In [54]:
sourcepath_json='/vol/atlas/databases/3DMD_SCIENSE_MUSEUM/'
dirs=os.listdir('/vol/phoebe/NEW_3DMD/')
r = re.compile('.._.._....')
days=[x for x in dirs if r.match(x) is not None]
subjects=[]
for day in days:
    tmplist=os.listdir('/vol/phoebe/NEW_3DMD/'+day)
    tmplist=[os.path.join('/vol/phoebe/NEW_3DMD/',day,x,'meshes') for x in tmplist if x!='backupjson']
    subjects.append(tmplist)
list_jsons=[]
for month in subjects:
    for sub in month:
        list_jsons.append(os.path.join(sourcepath_json,*sub.split('/')[-3:-1],sub.split('/')[-2]+'.json'))
for json_file in list_jsons:
    with open(json_file) as data_file:    
                data = json.load(data_file)
                print(json_file.split('/')[-2],data['sequenceframelast'])
                data_file.close() 
    

['/vol/atlas/databases/3DMD_SCIENSE_MUSEUM/14_04_2017/00355/00355.json', '/vol/atlas/databases/3DMD_SCIENSE_MUSEUM/14_04_2017/00411/00411.json', '/vol/atlas/databases/3DMD_SCIENSE_MUSEUM/14_04_2017/00389/00389.json', '/vol/atlas/databases/3DMD_SCIENSE_MUSEUM/14_04_2017/00367/00367.json', '/vol/atlas/databases/3DMD_SCIENSE_MUSEUM/14_04_2017/00346/00346.json', '/vol/atlas/databases/3DMD_SCIENSE_MUSEUM/14_04_2017/00408/00408.json', '/vol/atlas/databases/3DMD_SCIENSE_MUSEUM/14_04_2017/00402/00402.json', '/vol/atlas/databases/3DMD_SCIENSE_MUSEUM/14_04_2017/00374/00374.json', '/vol/atlas/databases/3DMD_SCIENSE_MUSEUM/14_04_2017/00390/00390.json', '/vol/atlas/databases/3DMD_SCIENSE_MUSEUM/14_04_2017/00373/00373.json', '/vol/atlas/databases/3DMD_SCIENSE_MUSEUM/14_04_2017/00397/00397.json', '/vol/atlas/databases/3DMD_SCIENSE_MUSEUM/14_04_2017/00379/00379.json', '/vol/atlas/databases/3DMD_SCIENSE_MUSEUM/14_04_2017/00405/00405.json', '/vol/atlas/databases/3DMD_SCIENSE_MUSEUM/14_04_2017/00341/0034

In [44]:
print(int('10'))

10


In [ ]:
printonekey(['Id','DateBirth'],below_2)

In [ ]:
nogender=searchnogender(list_of_hashes)
print(len(nogender))
printonekey(['Id','Gender','Email'],nogender)

In [ ]:
males=searchidn('Male', list_of_hashes)
females=searchidn('Female', list_of_hashes)
no_gender=searchidn('Other', list_of_hashes)
print('There are',len(males),'males', len(females),'females and',len(no_gender),'others')
print('Total: ',len(no_gender)+len(males)+len(females))


In [ ]:
t=[]
t=[x for x in os.listdir('/vol/phoebe/NEW_3DMD/10_04_2017/00053/meshes') if x.split('.')[-1]=='bmp']
# print(x)
# tmp[1].split('.')[2]
# for x in tmp:
#     if x.split('.')[2]=='bmp':
#         t.append(x)
print(sorted(t)[0].split('.')[1])
# print(t)

In [ ]:
(not_found, copied) = copy_obj_bmp2jpg_files(root_path,dest_path,above60white)

In [ ]:
print(len(list_of_hashes))
i=1
tmp_num=list_of_hashes[0]['Id']
tmp_list=list_of_hashes[1:]
for person in tmp_list:
    if  person['Id']-tmp_num!=1:
        print( person['Id'])
        i+=1
    tmp_num=person['Id']

<p><b> Extract obj and jpg files from specific people</b></p>
<b> Number 207, 208, 468,703, 759, 1617, 1618 are missing from Google Spreadsheets.</b>

In [ ]:
root_path='/vol/phoebe/3DMD_SCIENCE_MUSEUM/'
# root_path='/vol/phoebe/NEW_3DMD/'
# root_path='/vol/atlas/databases/3DMD_SCIENSE_MUSEUM/'
dest_path='/data/Dropbox/Dropbox/Dropbox/females/'
# spreadsheet_name= "Copy Museum data"
#
# list_of_hashes=read_google_sheets(spreadsheet_name)
print('List has been read')
# above60white=searchdate(1967,list_of_hashes)
# num_not_found, num_copied = copy_obj_bmp2jpg_files(root_path,dest_path,above60white)

# nogender=searchnogender(list_of_hashes)
num_not_found, num_copied,list_notfound = copy_obj_bmp2jpg_files(root_path,dest_path,females)
print(num_copied,' were copied')

In [ ]:
debug

<b>Export thumbnails by 4G<b>

In [ ]:
import menpo.io as mio

from menpo.visualize import print_progress
from pathlib import Path

def process_image(im):
    im = im.rescale_to_diagonal(700)
    subject_id = im.path.stem.split('.')[0]
    path =  Path('tmp') / subject_id / im.path.with_suffix('.jpg').name
    
    try:
        mio.export_image(im, path, overwrite=True)
    except:
        path.parent.mkdir(exist_ok=True, parents=True)
        mio.export_image(im, path)

# for im in print_progress(mio.import_images('/media/ap112/Seagate Expansion Drive/11_06_2017/**/meshes/*.bmp')):


In [ ]:
from multiprocessing import Pool

pool = Pool(4)

pool.map_async(process_image, mio.import_images('/media/ap112/Seagate Expansion Drive/11_06_2017/**/meshes/*.bmp'))

In [ ]:
pool.map_async()